# Importing the Necessary Packages and Modules

In [81]:
import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

print('Libraries imported.')

Libraries imported.


# Reading the Currently Available Data

In [2]:
df = pd.read_csv('Added_Lat_Lng_Coordinates.csv')

In [3]:
df['Borough'].value_counts()

North York          24
Downtown Toronto    18
Scarborough         17
Etobicoke           12
Central Toronto      9
West Toronto         6
York                 5
East Toronto         5
East York            5
Queen's Park         1
Mississauga          1
Name: Borough, dtype: int64

# Filtering for Neighbourhoods only with Toronto

In [4]:
df = df[df['Borough'].isin(['Downtown Toronto' , 'Central Toronto' , 'West Toronto' , 'East Toronto'])]

In [5]:
df.reset_index(inplace = True , drop =True)

In [6]:
df.head()

Postcode           Borough             Neighbourhood   Latitude  Longitude
0      M5A  Downtown Toronto  Harbourfront,Regent Park  43.654260 -79.360636
1      M5B  Downtown Toronto   Ryerson,Garden District  43.657162 -79.378937
2      M5C  Downtown Toronto            St. James Town  43.651494 -79.375418
3      M4E      East Toronto               The Beaches  43.676357 -79.293031
4      M5E  Downtown Toronto               Berczy Park  43.644771 -79.373306

# Folium Plots

In [7]:

# Toronto Latitude and Longitude : 43.651070, -79.347015
latitude = 43.651070
longitude = -79.347015
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=12)

# add markers to map
for lat, lng, borough, neighborhood in zip(df['Latitude'], df['Longitude'], df['Borough'], df['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

# Four Square API

In [46]:
CLIENT_ID = 'MW3FLO1DBILBVYR4WHLZJV32FSDHR2ASHF0SKDU0F2ICS14F' # your Foursquare ID
CLIENT_SECRET = 'B2PRIJH2SC4GXXZ23ZFP5KXZZEL4SJW4YAFKJKE5J1VMEP3P' # your Foursquare Secret
VERSION = '20191020' # Foursquare API version
LIMIT = 100
RADIUS = 1000
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: MW3FLO1DBILBVYR4WHLZJV32FSDHR2ASHF0SKDU0F2ICS14F
CLIENT_SECRET:B2PRIJH2SC4GXXZ23ZFP5KXZZEL4SJW4YAFKJKE5J1VMEP3P


In [31]:
url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(CLIENT_ID ,
                                                                                                        CLIENT_SECRET,
                                                                                                       VERSION,
                                                                                                       latitude,
                                                                                                       longitude,
                                                                                                        RADIUS,
                                                                                                        LIMIT)

In [32]:
url

'https://api.foursquare.com/v2/venues/explore?client_id=MW3FLO1DBILBVYR4WHLZJV32FSDHR2ASHF0SKDU0F2ICS14F&client_secret=B2PRIJH2SC4GXXZ23ZFP5KXZZEL4SJW4YAFKJKE5J1VMEP3P&v=20191020&ll=43.65107,-79.347015&radius=1000&limit=100'

In [34]:
results = requests.get(url).json()


# Getting the Data , Extracting what's needed and Putting it together

In [35]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [39]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name                categories        lat        lng
0               BATLgrounds        Athletics & Sports  43.647088 -79.351306
1               Souk Tabule  Mediterranean Restaurant  43.653756 -79.354390
2  Cirque du Soleil - LUZIA                    Circus  43.644791 -79.351000
3            Underpass Park                      Park  43.655764 -79.354806
4       The Broadview Hotel                     Hotel  43.659060 -79.350030

In [40]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

77 venues were returned by Foursquare.


# Getting all the Data for all the Neighbourhoods in Toronto

In [47]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            RADIUS, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [48]:
toronto = getNearbyVenues(names=df['Neighbourhood'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )


Harbourfront,Regent Park
Ryerson,Garden District
St. James Town
The Beaches
Berczy Park
Central Bay Street
Christie
Adelaide,King,Richmond
Dovercourt Village,Dufferin
Harbourfront East,Toronto Islands,Union Station
Little Portugal,Trinity
The Danforth West,Riverdale
Design Exchange,Toronto Dominion Centre
Brockton,Exhibition Place,Parkdale Village
The Beaches West,India Bazaar
Commerce Court,Victoria Hotel
Studio District
Lawrence Park
Roselawn
Davisville North
Forest Hill North,Forest Hill West
High Park,The Junction South
North Toronto West
The Annex,North Midtown,Yorkville
Parkdale,Roncesvalles
Davisville
Harbord,University of Toronto
Runnymede,Swansea
Moore Park,Summerhill East
Chinatown,Grange Park,Kensington Market
Deer Park,Forest Hill SE,Rathnelly,South Hill,Summerhill West
CN Tower,Bathurst Quay,Island airport,Harbourfront West,King and Spadina,Railway Lands,South Niagara
Rosedale
Stn A PO Boxes 25 The Esplanade
Cabbagetown,St. James Town
First Canadian Place,Underground city


In [49]:
len(df)

38

In [52]:
toronto.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Harbourfront,Regent Park               43.65426              -79.360636   
1  Harbourfront,Regent Park               43.65426              -79.360636   
2  Harbourfront,Regent Park               43.65426              -79.360636   
3  Harbourfront,Regent Park               43.65426              -79.360636   
4  Harbourfront,Regent Park               43.65426              -79.360636   

                                             Venue  Venue Latitude  \
0                                 Roselle Desserts       43.653447   
1                                    Tandem Coffee       43.653559   
2  Toronto Cooper Koo Family Cherry St YMCA Centre       43.653191   
3                                   Impact Kitchen       43.656369   
4                 The Distillery Historic District       43.650244   

   Venue Longitude        Venue Category  
0       -79.362017                Bakery  
1       -79.361809           Coffee Shop  
2       -79.357947  Gym / Fitness Center  
3       -79.356980            Restaurant  
4       -79.359323         Historic Site

In [53]:
len(toronto)

3082

In [59]:
toronto.columns

Index(['Neighborhood', 'Neighborhood Latitude', 'Neighborhood Longitude',
       'Venue', 'Venue Latitude', 'Venue Longitude', 'Venue Category'],
      dtype='object')

# Grouping the data by Neighbourhoods

In [60]:
toronto.groupby(['Neighborhood'],as_index = False).count()

Neighborhood  Neighborhood Latitude  \
0                              Adelaide,King,Richmond                    100   
1                                         Berczy Park                    100   
2          Brockton,Exhibition Place,Parkdale Village                    100   
3   Business Reply Mail Processing Centre 969 Eastern                     47   
4   CN Tower,Bathurst Quay,Island airport,Harbourf...                     15   
5                          Cabbagetown,St. James Town                     41   
6                                  Central Bay Street                    100   
7             Chinatown,Grange Park,Kensington Market                    100   
8                                            Christie                    100   
9                                Church and Wellesley                    100   
10                      Commerce Court,Victoria Hotel                    100   
11                                         Davisville                    100   
12                                   Davisville North                    100   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...                     81   
14            Design Exchange,Toronto Dominion Centre                    100   
15                        Dovercourt Village,Dufferin                     66   
16              First Canadian Place,Underground city                    100   
17                 Forest Hill North,Forest Hill West                     48   
18                      Harbord,University of Toronto                    100   
19    Harbourfront East,Toronto Islands,Union Station                    100   
20                           Harbourfront,Regent Park                    100   
21                       High Park,The Junction South                    100   
22                                      Lawrence Park                      9   
23                            Little Portugal,Trinity                    100   
24                         Moore Park,Summerhill East                     59   
25                                 North Toronto West                     43   
26                              Parkdale,Roncesvalles                    100   
27                                           Rosedale                     24   
28                                           Roselawn                     23   
29                                  Runnymede,Swansea                     74   
30                            Ryerson,Garden District                    100   
31                                     St. James Town                    100   
32                    Stn A PO Boxes 25 The Esplanade                    100   
33                                    Studio District                    100   
34                  The Annex,North Midtown,Yorkville                    100   
35                                        The Beaches                     79   
36                      The Beaches West,India Bazaar                     73   
37                        The Danforth West,Riverdale                    100   

    Neighborhood Longitude  Venue  Venue Latitude  Venue Longitude  \
0                      100    100             100              100   
1                      100    100             100              100   
2                      100    100             100              100   
3                       47     47              47               47   
4                       15     15              15               15   
5                       41     41              41               41   
6                      100    100             100              100   
7                      100    100             100              100   
8                      100    100             100              100   
9                      100    100             100              100   
10                     100    100             100              100   
11                     100    100             100              100   
12        

In [62]:
print('There are {} uniques categories.'.format(len(toronto['Venue Category'].unique())))

There are 278 uniques categories.


# One Hot Encoding the Dataset

In [63]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhood'] = toronto['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Zoo  Accessories Store  Afghan Restaurant  Airport  Airport Lounge  \
0    0                  0                  0        0               0   
1    0                  0                  0        0               0   
2    0                  0                  0        0               0   
3    0                  0                  0        0               0   
4    0                  0                  0        0               0   

   American Restaurant  Amphitheater  Animal Shelter  Antique Shop  Aquarium  \
0                    0             0               0             0         0   
1                    0             0               0             0         0   
2                    0             0               0             0         0   
3                    0             0               0             0         0   
4                    0             0               0             0         0   

   Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0            0           0                    0                 0   
1            0           0                    0                 0   
2            0           0                    0                 0   
3            0           0                    0                 0   
4            0           0                    0                 0   

   Athletics & Sports  Auto Dealership  BBQ Joint  Bagel Shop  Bakery  Bank  \
0                   0                0          0           0       1     0   
1                   0                0          0           0       0     0   
2                   0                0          0           0       0     0   
3                   0                0          0           0       0     0   
4                   0                0          0           0       0     0   

   Bar  Baseball Field  Baseball Stadium  Basketball Stadium  Beach  \
0    0               0                 0                   0      0   
1    0               0                 0                   0      0   
2    0               0                 0                   0      0   
3    0               0                 0                   0      0   
4    0               0                 0                   0      0   

   Beach Bar  Beer Bar  Beer Store  Belgian Restaurant  Bistro  Board Shop  \
0          0         0           0                   0       0           0   
1          0         0           0                   0       0           0   
2          0         0           0                   0       0           0   
3          0         0           0                   0       0           0   
4          0         0           0                   0       0           0   

   Bookstore  Boutique  Brazilian Restaurant  Breakfast Spot  Brewery  \
0          0         0                     0               0        0   
1          0         0                     0               0        0   
2          0         0                     0               0        0   
3          0         0                     0               0        0   
4          0         0                     0               0        0   

   Bridal Shop  Bubble Tea Shop  Buffet  Building  Burger Joint  \
0            0                0       0         0             0   
1            0                0       0         0             0   
2            0                0       0         0             0   
3            0                0       0         0             0   
4            0                0       0         0             0   

   Burrito Place  Bus Line  Bus Stop  Business Service  Butcher  Café  \
0              0         0         0                 0        0     0   
1              0         0         0                 0        0     0   
2              0         0         0                 0        0     0   
3              0         0         0                 0        0     0   
4              0         0         0                 0        0     0   

   Cajun / Creol

In [64]:
toronto_onehot.shape

(3082, 278)

In [65]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood   Zoo  \
0                              Adelaide,King,Richmond  0.00   
1                                         Berczy Park  0.00   
2          Brockton,Exhibition Place,Parkdale Village  0.00   
3   Business Reply Mail Processing Centre 969 Eastern  0.00   
4   CN Tower,Bathurst Quay,Island airport,Harbourf...  0.00   
5                          Cabbagetown,St. James Town  0.00   
6                                  Central Bay Street  0.00   
7             Chinatown,Grange Park,Kensington Market  0.00   
8                                            Christie  0.00   
9                                Church and Wellesley  0.00   
10                      Commerce Court,Victoria Hotel  0.00   
11                                         Davisville  0.00   
12                                   Davisville North  0.00   
13  Deer Park,Forest Hill SE,Rathnelly,South Hill,...  0.00   
14            Design Exchange,Toronto Dominion Centre  0.00   
15                        Dovercourt Village,Dufferin  0.00   
16              First Canadian Place,Underground city  0.00   
17                 Forest Hill North,Forest Hill West  0.00   
18                      Harbord,University of Toronto  0.00   
19    Harbourfront East,Toronto Islands,Union Station  0.00   
20                           Harbourfront,Regent Park  0.00   
21                       High Park,The Junction South  0.00   
22                                      Lawrence Park  0.00   
23                            Little Portugal,Trinity  0.00   
24                         Moore Park,Summerhill East  0.00   
25                                 North Toronto West  0.00   
26                              Parkdale,Roncesvalles  0.01   
27                                           Rosedale  0.00   
28                                           Roselawn  0.00   
29                                  Runnymede,Swansea  0.00   
30                            Ryerson,Garden District  0.00   
31                                     St. James Town  0.00   
32                    Stn A PO Boxes 25 The Esplanade  0.00   
33                                    Studio District  0.00   
34                  The Annex,North Midtown,Yorkville  0.00   
35                                        The Beaches  0.00   
36                      The Beaches West,India Bazaar  0.00   
37                        The Danforth West,Riverdale  0.00   

    Accessories Store  Afghan Restaurant   Airport  Airport Lounge  \
0                0.00               0.00  0.000000        0.000000   
1                0.00               0.00  0.000000        0.000000   
2                0.01               0.00  0.000000        0.000000   
3                0.00               0.00  0.000000        0.000000   
4                0.00               0.00  0.066667        0.066667   
5                0.00               0.00  0.000000        0.000000   
6                0.00               0.00  0.000000        0.000000   
7                0.00               0.00  0.000000        0.000000   
8                0.00               0.00  0.000000        0.000000   
9                0.00               0.01  0.000000        0.000000   
10               0.00               0.00  0.000000        0.000000   
11               0.00               0.00  0.000000        0.000000   
12               0.00               0.00  0.000000        0.000000   
13               0.00               0.00  0.000000        0.000000   
14               0.00               0.00  0.000000        0.000000   
15               0.00               0.00  0.000000        0.000000   
16               0.00               0.00  0.000000        0.000000   
17               0.00               0.00  0.000000        0.000000   
18               0.00               0.00  0.000000        0.000000   
19               0.00               0.00  0.000000        0.000000   
20               0.00               0.00  0.000000        0.000000   
21               0.00               0.00  0

# Observing Top 5 Venues

In [66]:
num_top_venues = 5

for hood in toronto_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide,King,Richmond----
                 venue  freq
0                 Café  0.07
1          Coffee Shop  0.06
2                Hotel  0.05
3              Theater  0.04
4  Japanese Restaurant  0.03


----Berczy Park----
          venue  freq
0   Coffee Shop  0.10
1          Café  0.06
2         Hotel  0.05
3      Beer Bar  0.04
4  Cocktail Bar  0.03


----Brockton,Exhibition Place,Parkdale Village----
                    venue  freq
0                    Café  0.08
1             Coffee Shop  0.06
2              Restaurant  0.05
3                     Bar  0.04
4  Furniture / Home Store  0.04


----Business Reply Mail Processing Centre 969 Eastern----
                venue  freq
0                Park  0.09
1             Brewery  0.06
2         Pizza Place  0.06
3         Coffee Shop  0.06
4  Italian Restaurant  0.04


----CN Tower,Bathurst Quay,Island airport,Harbourfront West,King and Spadina,Railway Lands,South Niagara----
              venue  freq
0              Café  0.13
1    

# Putting that into a DataFrame

In [67]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [68]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                             Adelaide,King,Richmond                  Café   
1                                        Berczy Park           Coffee Shop   
2         Brockton,Exhibition Place,Parkdale Village                  Café   
3  Business Reply Mail Processing Centre 969 Eastern                  Park   
4  CN Tower,Bathurst Quay,Island airport,Harbourf...           Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0           Coffee Shop                 Hotel               Theater   
1                  Café                 Hotel              Beer Bar   
2           Coffee Shop            Restaurant                   Bar   
3               Brewery           Coffee Shop           Pizza Place   
4                  Café       Harbor / Marina          Dance Studio   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0        Sushi Restaurant   Japanese Restaurant         Deli / Bodega   
1              Restaurant          Cocktail Bar    Italian Restaurant   
2  Furniture / Home Store                Bakery        Sandwich Place   
3               Pet Store      Sushi Restaurant         Burrito Place   
4                  Garden        Scenic Lookout                 Track   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0                   Bar        Cosmetics Shop           Concert Hall  
1   Japanese Restaurant                  Park                 Bakery  
2    Tibetan Restaurant   Arts & Crafts Store                   Park  
3    Italian Restaurant                 Diner             Restaurant  
4                  Park               Dog Run       Sculpture Garden

# K-Means Clustering 

In [69]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 0, 3, 4, 3, 3, 0, 0, 3], dtype=int32)

In [74]:
# add clustering labels
#neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = toronto

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged.head() # check the last columns!

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Harbourfront,Regent Park               43.65426              -79.360636   
1  Harbourfront,Regent Park               43.65426              -79.360636   
2  Harbourfront,Regent Park               43.65426              -79.360636   
3  Harbourfront,Regent Park               43.65426              -79.360636   
4  Harbourfront,Regent Park               43.65426              -79.360636   

                                             Venue  Venue Latitude  \
0                                 Roselle Desserts       43.653447   
1                                    Tandem Coffee       43.653559   
2  Toronto Cooper Koo Family Cherry St YMCA Centre       43.653191   
3                                   Impact Kitchen       43.656369   
4                 The Distillery Historic District       43.650244   

   Venue Longitude        Venue Category  Cluster Labels  \
0       -79.362017                Bakery               3   
1       -79.361809           Coffee Shop               3   
2       -79.357947  Gym / Fitness Center               3   
3       -79.356980            Restaurant               3   
4       -79.359323         Historic Site               3   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0           Coffee Shop                  Café               Theater   
1           Coffee Shop                  Café               Theater   
2           Coffee Shop                  Café               Theater   
3           Coffee Shop                  Café               Theater   
4           Coffee Shop                  Café               Theater   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0    Italian Restaurant                  Park                 Diner   
1    Italian Restaurant                  Park                 Diner   
2    Italian Restaurant                  Park                 Diner   
3    Italian Restaurant                  Park                 Diner   
4    Italian Restaurant                  Park                 Diner   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0            Restaurant                Bakery        Breakfast Spot   
1            Restaurant                Bakery        Breakfast Spot   
2            Restaurant                Bakery        Breakfast Spot   
3            Restaurant                Bakery        Breakfast Spot   
4            Restaurant                Bakery        Breakfast Spot   

  10th Most Common Venue  
0     Mexican Restaurant  
1     Mexican Restaurant  
2     Mexican Restaurant  
3     Mexican Restaurant  
4     Mexican Restaurant

# Finally Visualizing This

In [80]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Venue Latitude'], toronto_merged['Venue Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

# Observing the clusters

In [79]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighborhood Latitude  Venue Longitude                   Venue Category  \
579               43.669542       -79.420485                    Grocery Store   
580               43.669542       -79.426105                             Café   
581               43.669542       -79.420466                             Park   
582               43.669542       -79.421400                      Coffee Shop   
583               43.669542       -79.426148               Italian Restaurant   
584               43.669542       -79.421911                Indian Restaurant   
585               43.669542       -79.426541                            Diner   
586               43.669542       -79.422164                     Cocktail Bar   
587               43.669542       -79.424929        South American Restaurant   
588               43.669542       -79.415579                     Dessert Shop   
589               43.669542       -79.416640                      Coffee Shop   
590               43.669542       -79.423709                              Pub   
591               43.669542       -79.417093                Korean Restaurant   
592               43.669542       -79.428054                       Restaurant   
593               43.669542       -79.425183                     Cocktail Bar   
594               43.669542       -79.415746                Korean Restaurant   
595               43.669542       -79.413261                    Design Studio   
596               43.669542       -79.416954                       Taco Place   
597               43.669542       -79.423390                         Wine Bar   
598               43.669542       -79.419938                             Café   
599               43.669542       -79.422671             Ethiopian Restaurant   
600               43.669542       -79.413150                             Café   
601               43.669542       -79.413028                      Pizza Place   
602               43.669542       -79.413110                   Sandwich Place   
603               43.669542       -79.425076                      Comedy Club   
604               43.669542       -79.412726                              Spa   
605               43.669542       -79.416960                      Coffee Shop   
606               43.669542       -79.428099                     Cupcake Shop   
607               43.669542       -79.426471                             Café   
608               43.669542       -79.414230                        Gift Shop   
609               43.669542       -79.413845        Latin American Restaurant   
610               43.669542       -79.427099                      Music Store   
611               43.669542       -79.421646                Indian Restaurant   
612               43.669542       -79.416035                              Gym   
613               43.669542       -79.411777    Vegetarian / Vegan Restaurant   
614               43.669542       -79.418651                      Pizza Place   
615               43.669542       -79.415399                       Playground   
616               43.669542       -79.416340                    Grocery Store   
617               43.669542       -79.419297                             Café   
618               43.669542       -79.412022                           School   
619               43.669542       -79.416652                Korean Restaurant   
620               43.669542       -79.411898                Health Food Store   
621               43.669542       -79.423344                     Cocktail Bar   
622               43.669542       -79.411818                    Deli / Bodega   
623               43.669542       -79.424931                             Café   
624               43.669542       -79.414504                    Grocery Store   
625               43.669542       -79.414367                Korean Restaurant   
626               43.669542       -79.415007               Mexican Restaurant   
627               43.669542       -79